In [383]:
import pandas as pd
import numpy as np
import geopandas as gpd
import os
import altair as alt
import eco_style
import json
alt.themes.enable("light")

ThemeRegistry.enable('light')

In [384]:
df = pd.read_excel("labourproductivityitls.xls", sheet_name="A5", skiprows=4)
df = df.melt(id_vars=["ITL_level", "ITL_code", "Region_name"], var_name="year", value_name="value")
df = df.dropna(subset=["value"])
df['year'] = df['year'].str[-4:].astype(int)
full_df = df.copy()
df = df.query("ITL_level == 'ITL3'")
full_itl3_df = df.copy()

In [385]:
gdf = gpd.read_file("International_Territorial_Level_3_January_2021_UK_BUC_V3_2022_-1278520424922859526.geojson")
itl3_base = gdf.copy()

# MAP: Average earnings by LAD

In [536]:
# Load your original GeoDataFrame
gdf = gpd.read_file("Local_Authority_Districts_May_2024_Boundaries_UK_BUC_3499872675230401373")

# Standardise ID column
gdf = gdf.rename(columns={"LAD24CD": "id"})

# Create a 'country' code column (1st character of ID)
gdf['country'] = gdf['id'].str[:1]

# Step 1: Filter Northern Ireland rows (IDs starting with 'N')
ni_gdf = gdf[gdf['country'] == 'N']

# Step 2: Dissolve Northern Ireland into a single polygon
ni_dissolved = ni_gdf.dissolve(as_index=False)

# Step 3: Assign desired ID and name
ni_dissolved['id'] = 'N92000002'
ni_dissolved['LAD24NM'] = 'Northern Ireland'

# Step 4: Keep the rest of the UK (non-NI areas)
gdf_rest = gdf[gdf['country'] != 'N']

# Step 5: Combine into final GeoDataFrame
gdf_merged = pd.concat([gdf_rest, ni_dissolved], ignore_index=True)

gdf = gdf_merged.copy()

In [538]:


df = pd.read_excel("datadownload-2.xlsx", skiprows=8)
df.columns = ["name", "id", "median"]
uk_val = df.query("id == 'K02000001'")['median'].values[0]
df['median'] = pd.to_numeric(df['median'], errors='coerce')
df['value'] = (df['median'] / uk_val) -1

df = df.dropna(subset=["value"])

df = df.sort_values("value", ascending=False)
df['rank'] = np.arange(1, len(df) + 1)

df = pd.read_excel("ashetable72024provisional/PROV - Work Geography Table 7.1a   Weekly pay - Gross 2024.xlsx", sheet_name="Full-Time", skiprows=4)
df = df[["Description", "Code", "Median"]]
df.columns = ["name", "id", "median"]
uk_val = df.query("id == 'K02000001'")['median'].values[0]
df['median'] = pd.to_numeric(df['median'], errors='coerce')
df['value'] = (df['median'] / uk_val) -1

df = df.dropna(subset=["value"])

df = df.sort_values("value", ascending=False)
df['rank'] = np.arange(1, len(df) + 1)
df





gdf = gdf.merge(df, on="id", how="left")
gdf = gdf.query("name != 'Orkney Islands' and name != 'Shetland Islands'")

gdf


id               LAD24NM        LAD24NMW   BNG_E   BNG_N     LONG  \
0    E06000001            Hartlepool            None  447161  531473 -1.27017   
1    E06000002         Middlesbrough            None  451141  516887 -1.21099   
2    E06000003  Redcar and Cleveland            None  464330  519596 -1.00656   
3    E06000004      Stockton-on-Tees            None  444940  518179 -1.30664   
4    E06000005            Darlington            None  428029  515648 -1.56835   
..         ...                   ...             ...     ...     ...      ...   
346  W06000021         Monmouthshire       Sir Fynwy  337812  209231 -2.90280   
347  W06000022               Newport       Casnewydd  337897  187432 -2.89769   
348  W06000023                 Powys           Powys  302329  273254 -3.43531   
349  W06000024        Merthyr Tydfil  Merthyr Tudful  305916  206404 -3.36425   
350  N92000002      Northern Ireland            None  130813  541285 -6.17760   

         LAT                              GlobalID  \
0    54.6761  3f58aa35-9ea6-4001-a80f-8aab0e41313f   
1    54.5447  c5bc1c3e-111f-46db-8e41-362fbbc78d30   
2    54.5675  29afa1cb-8719-44c2-9906-38bc7bae2981   
3    54.5569  8ebb86c0-86bb-466e-ae7e-a832eeb755ff   
4    54.5353  bf2173db-02e1-4b58-9617-e775100f58ec   
..       ...                                   ...   
346  51.7783  46cfbd32-dcb3-4da1-a166-0f149baa4e24   
347  51.5823  2d467913-8823-4be7-9178-ced94fc0673a   
348  52.3486  1f185fde-3f8c-4e60-b45d-4fb0379a9a51   
349  51.7484  9925511b-44e7-4753-8da5-72e7e510b305   
350  54.6939  e975b970-33f7-44d8-9b55-20a19748b881   

                                              geometry country  index  \
0    POLYGON ((448964.105 536757.184, 448986.025 53...       E    NaN   
1    POLYGON ((451894.299 521145.303, 453997.697 51...       E    NaN   
2    POLYGON ((478232.947 518788.803, 477689.303 51...       E    NaN   
3    POLYGON ((452243.536 526335.188, 451711.3 5256...       E    NaN   
4    POLYGON ((436388.002 522354.197, 437351.702 52...       E    NaN   
..                                                 ...     ...    ...   
346  MULTIPOLYGON (((354639.302 191757.499, 354620....       W    NaN   
347  POLYGON ((343091.268 184213.081, 339999.991 18...       W    NaN   
348  POLYGON ((322891.603 333139.299, 323688.497 33...       W    NaN   
349  POLYGON ((308057.304 211036.201, 308367.104 20...       W    NaN   
350  MULTIPOLYGON (((94066.081 488462.84, 92861.178...       N    0.0   

                                name  median     value   rank  
0                      Hartlepool UA   698.0 -0.041604  185.0  
1                   Middlesbrough UA   626.1 -0.140327  358.0  
2            Redcar and Cleveland UA   666.4 -0.084992  271.0  
3                Stockton-on-Tees UA   616.6 -0.153371  370.0  
4                      Darlington UA   636.3 -0.126322  336.0  
..                               ...     ...       ...    ...  
346        Monmouthshire / Sir Fynwy   717.9 -0.014280  146.0  
347              Newport / Casnewydd   661.1 -0.092270  293.0  
348                    Powys / Powys   624.9 -0.141974  360.0  
349  Merthyr Tydfil / Merthyr Tudful   590.4 -0.189345  390.0  
350                Northern Ireland    666.1 -0.085404  273.0  

[349 rows x 15 columns]

In [566]:



to_label = [
    "City of London", 
    "Pendle",
    "Torridge",
    "Merthyr Tydfil / Merthyr Tudful",
    "East Dunbartonshire"
]


labels = {
    "City of London": "London",
    "Pendle": "Pendle",
    "Torridge": "Torridge",
    "Merthyr Tydfil / Merthyr Tudful": "Merthyr Tydfil",
    "East Dunbartonshire": "E. Dunbartonshire"
}

alignments = {
    "City of London": "left",
    "Pendle": "left",
    "Torridge": "right",
    "Merthyr Tydfil / Merthyr Tudful": "right",
    "East Dunbartonshire": "left"
}

dxs = {
    "City of London": 0,
}

dys = {
    "Pendle": 0,
}

gdf['name'] = gdf['name'].str.strip()
gdf['label_text'] = gdf['name'].apply(lambda x: labels[x].upper() if x in labels else x)
gdf['to_label'] = gdf['name'].isin(to_label)
# gdf['label_text'] = gdf['label_text'].apply(lambda x: x.upper() if isinstance(x, str) else [s.upper() for s in x])

gdf["LAT"] = gdf.geometry.centroid.y
gdf["LONG"] = gdf.geometry.centroid.x

choropleth = alt.Chart(gdf).mark_geoshape(
    opacity=0.9,
    stroke="rgba(0, 0, 0, 0.1)",
    strokeWidth=0.1,
).encode(
    color=alt.Color("value:Q", 
                    legend=alt.Legend(
                        labelFontWeight="lighter",
                        labelFont="Arial",
                        labelFontSize=15,
                        values=[-0.25, 0, 0.25],
                        labelExpr="""
                            datum.value == 0 ? 'UK average' :
                            datum.value == -0.7 ? datum.label + '' :
                            datum.value == 0.7 ? datum.label + ' ' :
                            format(datum.value, ',.0%')
                        """,
                        orient='none',
                        legendY=620,
                        legendX=180,
                        gradientLength=230,
                        direction='horizontal',

                            # datum.value == 0.6 ? '60%' :
                            # datum.value == -0.4 ? '-40%' :
                        format=",.0%",
                    ),
                    scale=alt.Scale(
                        # range=["#36B7B4", "#C9C9C9", "#E6224B"],
                        # range=[
                        #        "rgb(165,39,71)",
                        #         "rgb(255,255,224)",
                        #         "rgb(27,87,150)",],
                                                range=[
                               "rgb(198,81,71)",
                                "rgb(255,255,224)",
                                "rgb(58,121,168)",],

                                               domain=[-0.25, 0, 0.25],
                                                reverse=False), title=""),
    tooltip=[
        alt.Tooltip("name:N", title="Region"),
        alt.Tooltip("value:Q", format=",.0%", title="Productivity relative to UK average (2022)"),
    ],
).project(
    type="identity",
    reflectY=True,
)

labels = alt.Chart(gdf).mark_text(
    align=alt.expr(f'{json.dumps(alignments)}[datum.name]'),
    baseline='middle',
    # stroke='rgb(225,225,225 )',
    # strokeWidth=0.25,
    font='Arial',
    fontSize=15,
    fontWeight='lighter',
    opacity=0.8,
    dx=alt.expr(f"{json.dumps(alignments)}[datum.name] === 'left' ? 5 : -5"),
    dy=alt.expr(f"{json.dumps(dys)}[datum.name] || 0"),
    color='black'
).encode(
    longitude=alt.X('LONG:Q', title=None),
    latitude=alt.Y('LAT:Q', title=None),
    text=alt.Text('label_text:N'),
).transform_filter(
    alt.FieldOneOfPredicate(field='name', oneOf=to_label)
)

label_points = alt.Chart(gdf).mark_circle(
    size=15,
    color='black',
    opacity=1
).encode(
    longitude=alt.X('LONG:Q', title=None),
    latitude=alt.Y('LAT:Q', title=None),
).transform_filter(
    "datum.to_label == true"
)


chart = choropleth + labels + label_points

chart = chart.properties(
    width=500,
    height=600,
)

chart.save("avg_earnings_relative_to_uk_average.json")
chart.save("avg_earnings_relative_to_uk_average.png", scale_factor=5)
chart


/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=Fa

alt.LayerChart(...)

In [559]:
gdf.query("id == 'E07000122'").iloc[0]['name']

'  Pendle'

In [552]:
gdf.sort_values("value", ascending=False).tail(50)

id                  LAD24NM        LAD24NMW   BNG_E   BNG_N  \
309  S12000026         Scottish Borders            None  345889  626137   
248  E08000023           South Tyneside            None  435505  564057   
231  E08000005                 Rochdale            None  390315  412326   
164  E07000145           Great Yarmouth            None  646762  315881   
48   E06000052                 Cornwall            None  212497   64493   
79   E07000043              North Devon            None  265112  132533   
146  E07000127          West Lancashire            None  342606  413271   
210  E07000225               Chichester            None  490285  116600   
323  S12000045      East Dunbartonshire            None  261240  676154   
69   E07000033                 Bolsover            None  448666  371547   
204  E07000219    Nuneaton and Bedworth            None  435420  289352   
173  E07000174                Mansfield            None  455047  363637   
1    E06000002            Middlesbrough            None  451141  516887   
334  W06000008               Ceredigion      Ceredigion  267127  268437   
348  W06000023                    Powys           Powys  302329  273254   
43   E06000046            Isle of Wight            None  447183   85949   
166  E07000147            North Norfolk            None  611043  330857   
99   E07000076                 Tendring            None  614190  222141   
155  E07000136                   Boston            None  526851  343956   
8    E06000009                Blackpool            None  332817  436635   
170  E07000171                Bassetlaw            None  468073  384835   
244  E08000018                Rotherham            None  447542  388980   
227  E08000001                   Bolton            None  368352  409874   
329  W06000002                  Gwynedd         Gwynedd  280555  334966   
3    E06000004         Stockton-on-Tees            None  444940  518179   
150  E07000131               Harborough            None  474550  293873   
161  E07000142             West Lindsey            None  499314  390326   
103  E07000080           Forest of Dean            None  367175  212759   
152  E07000133                   Melton            None  477328  323469   
331  W06000004             Denbighshire    Sir Ddinbych  309843  355416   
234  E08000008                 Tameside            None  394987  397995   
87   E07000064                   Rother            None  578721  119666   
44   E06000047            County Durham            None  410383  532242   
144  E07000125               Rossendale            None  382827  420953   
80   E07000044               South Hams            None  270672   54039   
26   E06000027                   Torbay            None  289730   64613   
236  E08000010                    Wigan            None  362139  402126   
187  E07000198  Staffordshire Moorlands            None  400543  352448   
330  W06000003                    Conwy           Conwy  283293  362563   
171  E07000172                 Broxtowe            None  449829  341891   
159  E07000140            South Holland            None  532910  322929   
136  E07000117                  Burnley            None  384886  430880   
82   E07000046                 Torridge            None  244206  114334   
147  E07000128                     Wyre            None  347294  445159   
349  W06000024           Merthyr Tydfil  Merthyr Tudful  305916  206404   
139  E07000120                 Hyndburn            None  374407  428967   
156  E07000137             East Lindsey            None  534861  376064   
154  E07000135        Oadby and Wigston            None  461543  299379   
141  E07000122                   Pendle            None  387638  443368   
49   E06000053          Isles of Scilly            None   91327   11447   

              LONG            LAT                              GlobalID  \
309  350373.816271  631626.740282  28a6a6db-0664-44b4-b6a7-08422cf97d74   
248  435729.267025  563155.694326  c

In [442]:
df.value.describe(percentiles=[0.05, 0.25, 0.5, 0.75, 0.95, 0.975, 0.99])

count    394.000000
mean      -0.027049
std        0.108634
min       -0.210490
5%        -0.155671
25%       -0.093368
50%       -0.051215
75%        0.022758
95%        0.165275
97.5%      0.208925
99%        0.306563
max        0.706302
Name: value, dtype: float64

# MAP: Productivity by region, 2022

In [567]:
df = pd.read_excel("labourproductivityitls.xls", sheet_name="A4", skiprows=4)
df = df.melt(id_vars=["ITL_level", "ITL_code", "Region_name"], var_name="year", value_name="value")
df = df.dropna(subset=["value"])
df['year'] = df['year'].str[-4:].astype(int)
uk_val = df.query("ITL_code == 'UKX' and year == 2022")['value'].values[0]
df = df.query("ITL_level == 'ITL3'")


df = itl3_base.merge(df, left_on="ITL321CD", right_on="ITL_code", how="left")
df['value'] = df['value']/uk_val
df = df.query("year == 2022")

df['value'] = df['value']-1

df['rank'] = df['value'].rank(method='min', ascending=False)
point_num = 8
df['top_or_bottom_ten'] = np.where((df['rank'] <= point_num )| (df['rank'] > (len(df) - point_num)), True, False)


to_label = [
    "Camden and City of London", 
    "Swindon",
    # "Berkshire",
    # "North Hampshire",
    "City of Edinburgh",
    # Pivot
    "Powys",
    "Torbay",
    "Gwynedd",
    "North Nottinghamshire",
    # "Na h-Eileanan Siar"
]

labels = {
    # "Camden and City of London": ["Camden &", "City of London"],
    "Camden and City of London": "London",
    "North Hampshire": "N Hampshire",
    "City of Edinburgh": "Edinburgh",
    "North Nottinghamshire": "N. NOTS",
    "Na h-Eileanan Siar": ["OUTER", "HEBRIDES"],
}

alignments = {
    "Camden and City of London": "left",
    "Swindon": "right",
    "Berkshire": "right",
    "North Hampshire": "right",
    "City of Edinburgh": "left",
    "Powys": "right",
    "Torbay": "right",
    "Gwynedd": "right",
    "North Nottinghamshire": "left",
    "Na h-Eileanan Siar": "right"
}

dxs = {
    "Camden and City of London": 5
}

dys = {
    "Swindon": 0,
    "North Hampshire": 3
}


df['label_text'] = df['Region_name'].apply(lambda x: labels[x] if x in labels else x)
df['label_text'] = df['label_text'].apply(lambda x: x.upper() if isinstance(x, str) else [s.upper() for s in x])

df = df.query("Region_name != 'Orkney Islands' and Region_name != 'Shetland Islands'")

choropleth = alt.Chart(df).mark_geoshape().encode(
    color=alt.Color("value:Q", 
                    legend=alt.Legend(
                        labelFontWeight="lighter",
                        labelFont="Arial",
                        labelFontSize=15,
                        values=[-0.7, -0.35, 0, 0.35, 0.7],
                        labelExpr="""
                            datum.value == 0 ? 'UK average' :
                            datum.value == -0.7 ? datum.label + '' :
                            datum.value == 0.7 ? datum.label + ' ' :
                            format(datum.value, ',.0%')
                        """,
                        orient='none',
                        legendY=620,
                        legendX=180,
                        gradientLength=230,
                        direction='horizontal',

                            # datum.value == 0.6 ? '60%' :
                            # datum.value == -0.4 ? '-40%' :
                        format=",.0%",
                    ),
                    scale=alt.Scale(
                        # range=["#36B7B4", "#C9C9C9", "#E6224B"],
                        # range=[
                        #        "rgb(165,39,71)",
                        #         "rgb(255,255,224)",
                        #         "rgb(27,87,150)",],
                                                range=[
                               "rgb(198,81,71)",
                                "rgb(255,255,224)",
                                "rgb(58,121,168)",],

                                               domain=[-0.7, 0, 0.7],
                                                reverse=False), title=""),
    tooltip=[
        alt.Tooltip("Region_name:N", title="Region"),
        alt.Tooltip("value:Q", format=",.0%", title="Productivity relative to UK average (2022)"),
    ],
)

labels = alt.Chart(df).mark_text(
    align=alt.expr(f'{json.dumps(alignments)}[datum.Region_name]'),
    baseline='middle',
    # stroke='rgb(225,225,225 )',
    # strokeWidth=0.25,
    font='Arial',
    fontSize=15,
    fontWeight='lighter',
    opacity=0.8,
    dx=alt.expr(f"{json.dumps(alignments)}[datum.Region_name] === 'left' ? 5 : -5"),
    dy=alt.expr(f"{json.dumps(dys)}[datum.Region_name] || 0"),
    color='black'
).encode(
    longitude=alt.X('LONG:Q', title=None),
    latitude=alt.Y('LAT:Q', title=None),
    text=alt.Text('label_text:N'),
).transform_filter(
    alt.FieldOneOfPredicate(field='Region_name', oneOf=to_label)
)

label_points = alt.Chart(df).mark_circle(
    size=15,
    color='black',
    opacity=1
).encode(
    longitude=alt.X('LONG:Q', title=None),
    latitude=alt.Y('LAT:Q', title=None),
).transform_filter(
    alt.FieldOneOfPredicate(field='Region_name', oneOf=to_label)
)

# .transform_filter(
#     "datum.top_or_bottom_ten == true"
# )



chart = choropleth + labels + label_points

chart = chart.properties(
    width=500,
    height=600,
)


chart.save("labour_productivity_per_itl3_2022.json")
chart.save("labour_productivity_per_itl3_2022.png", scale_factor=6)
chart

/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=Fa

alt.LayerChart(...)

# Bubbles: Productivity by region in 2022

In [183]:
df = pd.read_excel("labourproductivityitls.xls", sheet_name="A4", skiprows=4)
df = df.melt(id_vars=["ITL_level", "ITL_code", "Region_name"], var_name="year", value_name="value")
df = df.dropna(subset=["value"])
df['year'] = df['year'].str[-4:].astype(int)
uk_val = df.query("ITL_code == 'UKX' and year == 2022")['value'].values[0]
df = df.query("ITL_level == 'ITL3'")


df = itl3_base.merge(df, left_on="ITL321CD", right_on="ITL_code", how="left")
df['value'] = df['value']/uk_val
df = df.query("year == 2022")

df

OBJECTID ITL321CD                         ITL321NM   BNG_E   BNG_N  \
18           1    TLC11  Hartlepool and Stockton-on-Tees  444952  522016   
37           2    TLC12                   South Teesside  461718  519597   
56           3    TLC13                       Darlington  428029  515649   
75           4    TLC14                           Durham  410381  532242   
94           5    TLC21                   Northumberland  395323  600699   
...        ...      ...                              ...     ...     ...   
3324       175    TLN0C         Causeway Coast and Glens  106227  581413   
3343       176    TLN0D          Antrim and Newtownabbey  130876  541274   
3362       177    TLN0E          Lisburn and Castlereagh  138776  518906   
3381       178    TLN0F              Mid and East Antrim  134007  560141   
3400       179    TLN0G              Fermanagh and Omagh   41284  512998   

         LONG       LAT                              GlobalID  \
18   -1.30587  54.59135  ead72b3b-1395-4d1e-97f2-019efe9d5efc   
37   -1.04695  54.56785  9e67f60c-56d9-4d92-99d9-b8751a251f1a   
56   -1.56835  54.53535  19f6e0b6-1047-45eb-972b-b76c9c720bcf   
75   -1.84050  54.68513  b31e1cc9-90f2-4bdb-8e68-351a969befdf   
94   -2.07521  55.30037  44d118ac-a39f-4d88-b6bd-bb4eb814164d   
...       ...       ...                                   ...   
3324 -6.59867  55.03959  ad7ee21e-9338-44e3-857d-5162dcbc9b9e   
3343 -6.17661  54.69379  8123eeb6-6d6d-4590-b474-a34ed1ade4f4   
3362 -6.03445  54.49743  5b461958-5a4d-4118-8b51-bea94e5a2d2e   
3381 -6.14545  54.86456  a7f41894-3ec6-4c21-b8e8-e30e4e8079f3   
3400 -7.52630  54.38511  43041c67-0b26-42c6-9664-97aad892d4df   

                                               geometry ITL_level ITL_code  \
18    POLYGON ((-1.27025 54.72717, -1.25186 54.71962...      ITL3    TLC11   
37    POLYGON ((-1.00241 54.59359, -0.96029 54.58503...      ITL3    TLC12   
56    POLYGON ((-1.43836 54.59508, -1.42333 54.60313...      ITL3    TLC13   
75    POLYGON ((-1.55941 54.88204, -1.56181 54.87572...      ITL3    TLC14   
94    MULTIPOLYGON (((-1.77849 55.66792, -1.80244 55...      ITL3    TLC21   
...                                                 ...       ...      ...   
3324  MULTIPOLYGON (((-6.18892 55.25847, -6.19982 55...      ITL3    TLN0C   
3343  POLYGON ((-5.86723 54.6888, -5.89468 54.67398,...      ITL3    TLN0D   
3362  POLYGON ((-6.04453 54.60581, -6.04292 54.58607...      ITL3    TLN0E   
3381  POLYGON ((-5.86723 54.6888, -5.88878 54.69586,...      ITL3    TLN0F   
3400  POLYGON ((-6.93912 54.77353, -6.93987 54.75213...      ITL3    TLN0G   

                          Region_name  year     value  
18    Hartlepool and Stockton-on-Tees  2022  0.978049  
37                     South Teesside  2022  0.773171  
56                         Darlington  2022  0.753659  
75                          Durham CC  2022  0.860976  
94                     Northumberland  2022  0.873171  
...                               ...   ...       ...  
3324         Causeway Coast and Glens  2022  0.839024  
3343          Antrim and Newtownabbey  2022  0.978049  
3362          Lisburn and Castlereagh  2022  0.929268  
3381              Mid and East Antrim  2022  0.936585  
3400              Fermanagh and Omagh  2022  0.926829  

[179 rows x 14 columns]

In [390]:
df = pd.read_excel("labourproductivityitls.xls", sheet_name="A4", skiprows=4)
df = df.melt(id_vars=["ITL_level", "ITL_code", "Region_name"], var_name="year", value_name="value")
df = df.dropna(subset=["value"])
df['year'] = df['year'].str[-4:].astype(int)
df = df.query("ITL_level == 'ITL3'")
df['ITL1'] = df['ITL_code'].str[:3]
df['country'] = df['ITL1'].map({
    "TLM": "Scotland",
    "TLL": "Wales",
    "TLN": "Northern Ireland",
})
df['country'] = df['country'].fillna("England")
np.random.seed(42)
df['jitter'] = np.random.normal(0, 1, len(df))
df = df.query("year == 2022")

df['top_within_country'] = df.groupby('country')['value'].rank(method='min', ascending=False)
df['bottom_within_country'] = df.groupby('country')['value'].rank(method='max', ascending=True)
df['label'] = np.where(
    (df['top_within_country'] <= 1) | (df['bottom_within_country'] <= 1),
    df['Region_name'],
    ""
)


jitter_ammount = 15

def split_by_length(text, max_len=15):
    text = text.replace(" and ", " & ")
    words = text.split()
    
    lines = []
    current_line = ""
    
    for word in words:
        # Check if adding the word would exceed the max length
        if len(current_line) + len(word) + 1 > max_len:
            lines.append(current_line.strip().upper())
            current_line = word
        else:
            current_line += " " + word
    
    # Add the final line
    if current_line:
        lines.append(current_line.strip().upper())

    # Ensure max 3 lines
    if len(lines) > 3:
        # Merge extras into the 3rd line
        lines = lines[:2] + [' '.join(lines[2:]).upper()]

    return lines

df['label'] = df['label'].apply(lambda x: split_by_length(x) if isinstance(x, str) else x)

base = alt.Chart(df).encode(
    tooltip=[
        alt.Tooltip("Region_name:N", title="Region"),
        alt.Tooltip("value:Q", format=",.0%", title="Productivity relative to UK average (2022)"),
        alt.Tooltip("country:N", title="Country"),
    ],
    x=alt.X("value:Q", 
            scale=alt.Scale(
                domainMin=10
            ),
            axis=alt.Axis(
                labelFontSize=11,
                tickOpacity=0,
        labelExpr="'£'+datum.label"),),
    y=alt.Y("country:N", 
            title=None,
            axis=alt.Axis(
                labelFontSize=11,
                domain=False,),
            sort=["England", "Scotland", "Wales", "Northern Ireland"]),
    yOffset= alt.YOffset("jitter:Q", title=None, 
                         scale=alt.Scale()),
    color=alt.Color(
        "country:N",
        scale=alt.Scale(
            domain=['England', 'Wales', 'Scotland', 'Northern Ireland'],
            range=['#36b7b4', '#e6224b', '#0063AF', '#F4C245']
        ),
                legend=None,
)
)

circles = base.mark_circle(size=50)

labels = base.mark_text(
    fontSize=10,
    font='Arial',
    fontWeight='lighter',
    baseline='middle',
    opacity=1,
    align=alt.expr("datum.top_within_country <= 5 ? 'left' : 'right'"),
    dx=alt.expr("datum.top_within_country <= 5 ? 5 : -5"),
    dy=alt.expr("isArray(datum.label)? length(datum.label) * -3.5 : 0"),
    color="black",
).encode(
    text=alt.Text("label:N"),
)

chart = (circles + labels).properties(
    width=300,
    height=220,
)

chart.save("labour_productivity_per_itl3_2022_scatter.json")
chart.save("labour_productivity_per_itl3_2022_scatter.png", scale_factor=5)
chart

/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=Fa

alt.LayerChart(...)

In [378]:
{
    'England': '#36b7b4',
    'Wales': '#e6224b',
    'Scotland': '#0063AF',
    'Northern Ireland': '#F4C245'
}.values()

dict_values(['#36b7b4', '#e6224b', '#0063AF', '#F4C245'])

## Map: Change in productivity by region, 2008-2022

In [368]:
df = pd.read_excel("labourproductivityitls.xls", sheet_name="A5", skiprows=4)
df = df.melt(id_vars=["ITL_level", "ITL_code", "Region_name"], var_name="year", value_name="value")
df = df.dropna(subset=["value"])
df['year'] = df['year'].str[-4:].astype(int)
df = df.query("ITL_level == 'ITL3'")
df = df.query("year == 2022 or year == 2008")
df = df.pivot_table(index=["ITL_code", "Region_name"], columns="year", values="value").reset_index()
df['value'] = (df[2022]/ df[2008])-1
df = df[['ITL_code', 'Region_name', 'value']]






df = itl3_base.merge(df, left_on="ITL321CD", right_on="ITL_code", how="left")
df['rank'] = df['value'].rank(method='min', ascending=False)
point_num = 8
df['top_or_bottom_ten'] = np.where((df['rank'] <= point_num )| (df['rank'] > (len(df) - point_num)), True, False)

labels = {
    "Darlington": "Darlington",
    "Berkshire": "Berkshire",
    "West Lothian": "West Lothian",
    "Brighton and Hove": "Brighton and Hove",
    "Lisburn and Castlereagh": ["Lisburn and", "Castlereagh"],
    # 
    "Tower Hamlets": "London",
    "Derby": "Derby",
    "Mid and East Antrim": ["Mid & East", "Antrim"],
    "West Essex": "West Essex"
}

to_label = list(labels.keys())


alignments = {
    "Darlington": "left",
    "Berkshire": "right",
    "West Lothian": "left",
    "Brighton and Hove": "left",
    "Lisburn and Castlereagh": "left",
    # 
    "Tower Hamlets": "left",
    "Derby": "left",
    "Mid and East Antrim": "left",
    "West Essex": "left"
}

dxs = {
    "Camden and City of London": 5
}

dys = {
    "Swindon": -5,
    "North Hampshire": 3
}


df['label_text'] = df['Region_name'].apply(lambda x: labels[x] if x in labels else x)
df['label_text'] = df['label_text'].apply(lambda x: x.upper() if isinstance(x, str) else [s.upper() for s in x])

choropleth = alt.Chart(df).mark_geoshape().encode(
    color=alt.Color("value:Q", 
                    legend=alt.Legend(
                        labelFontWeight="lighter",
                        labelFont="Arial",
                        labelExpr="""
                            datum.value == 0 ? 'No change' :
                            datum.value == -0.7 ? datum.label + '' :
                            datum.value == 0.7 ? datum.label + ' ' :
                            format(datum.value, ',.0%')
                        """,
                        orient='none',
                        legendY=620,
                        legendX=180,
                        gradientLength=230,
                        labelAlign='center',
                        direction='horizontal',

                            # datum.value == 0.6 ? '60%' :
                            # datum.value == -0.4 ? '-40%' :
                        format=",.0%",
                    ),
                    scale=alt.Scale(
                        # range=["#36B7B4", "#C9C9C9", "#E6224B"],
                        # range=[
                        #        "rgb(165,39,71)",
                        #         "rgb(255,255,224)",
                        #         "rgb(27,87,150)",],
                                                range=[
                               "rgb(198,81,71)",
                                "rgb(255,255,224)",
                                "rgb(58,121,168)",],

                                            domainMid=0,
                                                reverse=False), title=""),
    tooltip=[
        alt.Tooltip("Region_name:N", title="Region"),
        alt.Tooltip("value:Q", format=",.0%", title="Productivity relative to UK average (2022)"),
    ],
)

labels = alt.Chart(df).mark_text(
    align=alt.expr(f'{json.dumps(alignments)}[datum.Region_name]'),
    baseline='middle',
    stroke='rgb(225,225,225 )',
    lineHeight=10,
    strokeWidth=0.25,
    fontSize=11,
    font='Arial',
    fontWeight='lighter',
    opacity=0.8,
    dx=alt.expr(f"{json.dumps(alignments)}[datum.Region_name] === 'left' ? 5 : -15"),
    dy=alt.expr(f"{json.dumps(dys)}[datum.Region_name] || 0"),
    color='black'
).encode(
    longitude=alt.X('LONG:Q', title=None),
    latitude=alt.Y('LAT:Q', title=None),
    text=alt.Text('label_text:N'),
).transform_filter(
    alt.FieldOneOfPredicate(field='Region_name', oneOf=to_label)
)

label_points = alt.Chart(df).mark_circle(
    size=15,
    color='black',
    opacity=1
).encode(
    longitude=alt.X('LONG:Q', title=None),
    latitude=alt.Y('LAT:Q', title=None),
).transform_filter(
    alt.FieldOneOfPredicate(field='Region_name', oneOf=to_label)
)

# .transform_filter(
#     "datum.top_or_bottom_ten == true"
# )



chart = choropleth + labels + label_points

chart = chart.properties(
    width=500,
    height=600,
)


chart.save("labour_productivity_change_per_itl3_2008_to_2022.json")
chart.save("labour_productivity_change_per_itl3_2008_to_2022.png", scale_factor=3)
chart


/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=Fa

alt.LayerChart(...)

# Chart: timeseries of productivity by region, 2008-2022


In [358]:
df = pd.read_excel("labourproductivityitls.xls", sheet_name="A5", skiprows=4)
df = df.melt(id_vars=["ITL_level", "ITL_code", "Region_name"], var_name="year", value_name="value")
df = df.dropna(subset=["value"])
df['year'] = df['year'].str[-4:].astype(int)
#df = df.query("ITL_level == 'ITL'")
df = df.query('Region_name == "England" or Region_name == "Wales" or Region_name == "Scotland" or Region_name == "Northern Ireland"')

df_2008 = df.query("year == 2008").rename(columns={"value": "value_2008"}).drop(columns=["year"])

df = df.merge(df_2008, on=["ITL_code", "Region_name", "ITL_level"], how="left") 
df['value'] = (df['value'] / df['value_2008'])*100
df['label'] = np.where(df['year'] == 2022, df.Region_name, "")

df['year'] = pd.to_datetime(df['year'], format='%Y')

df = df.query("year >= '2008-01-01'")

base = alt.Chart(df).encode(
    x=alt.X("year:T", title=None, axis=alt.Axis(format="%Y")),
    y=alt.Y("value:Q", title="", scale=alt.Scale(zero=False), axis=alt.Axis(
        labelExpr="datum.value == 100 ? '2008=100' : datum.label")),
    color=alt.Color("Region_name:N", legend=None),
)

lines = base.mark_line()

end_labels = base.mark_text(
    align='left',
    baseline='middle',
    dx=5,
    dy=alt.expr("datum.Region_name === 'Northern Ireland' ? -5 : datum.Region_name === 'Scotland' ? 5 : 0"),
    fontSize=10,
    opacity=0.8,
).encode(
    text=alt.Text("label:N"),
).transform_filter(
    "datum.label != ''"
)

chart = lines + end_labels
chart.save("labour_productivity_change_over_time.json")
chart.save("labour_productivity_change_over_time.png", scale_factor=3)


/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=Fa

In [318]:
df.sort_values("value", ascending=True).head(20)


OBJECTID ITL321CD                                 ITL321NM   BNG_E  \
84         85    TLI42                            Tower Hamlets  536345   
38         39    TLF11                                    Derby  435609   
89         90    TLI52          Barking & Dagenham and Havering  552765   
92         93    TLI61                                  Bromley  542036   
88         89    TLI51                     Bexley and Greenwich  546458   
177       178    TLN0F                      Mid and East Antrim  134007   
98         99    TLI74                    Harrow and Hillingdon  511841   
76         77    TLH35                               West Essex  555274   
57         58    TLG32                                 Solihull  419434   
94         95    TLI63  Merton, Kingston upon Thames and Sutton  524015   
90         91    TLI53             Redbridge and Waltham Forest  541591   
99        100    TLI75        Hounslow and Richmond upon Thames  512146   
83         84    TLI41                       Hackney and Newham  540488   
27         28    TLE11              Kingston upon Hull, City of  511894   
107       108    TLJ26                              East Surrey  527706   
79         80    TLI31                Camden and City of London  527620   
96         97    TLI72                                    Brent  519615   
117       118    TLJ43                      Kent Thames Gateway  593761   
134       135    TLL12                                  Gwynedd  277968   
74         75    TLH32                                 Thurrock  562126   

      BNG_N      LONG       LAT                              GlobalID  \
84   181451 -0.036400  51.51553  0a15a79e-bd9e-412e-af48-1c9065791af1   
38   335375 -1.471890  52.91464  3b676bbd-b8b3-4cbf-956a-4f5c7558aa38   
89   186559  0.202273  51.55723  833752e3-90b5-49d2-9b27-2663a5088a7b   
92   165708  0.039246  51.37267  4d6c57b8-2d18-42f1-b511-1210d86d4028   
88   175715  0.106862  51.46146  d7b319c0-971a-48dc-a9e1-3f0578834219   
177  560141 -6.145450  54.86456  a7f41894-3ec6-4c21-b8e8-e30e4e8079f3   
98   188359 -0.387190  51.58300  5d428a9c-86f7-4675-9d50-5b1f0d7429fa   
76   223275  0.254790  51.88642  cc266b2b-573a-40c8-a9b8-61a8ca61cdab   
57   281483 -1.715580  52.43100  93ba6ae4-3821-43b0-bdf1-39c1d42f7342   
94   166299 -0.219310  51.38220  2c58eeda-4cda-429e-8b9e-9318da1a548d   
90   190422  0.042757  51.59485  6babf09c-e315-462d-a528-6133e4138a00   
99   173382 -0.387550  51.44833  3d6dc79c-7f51-439d-bd60-8fa488e40c5a   
83   183989  0.024276  51.53732  d7171d51-a972-4a95-9601-b9e0c65b15c2   
27   431716 -0.303800  53.76979  5287663a-16a4-4ac2-8f28-3d91153d7c5b   
107  150601 -0.171910  51.24030  8df70722-08c7-4d32-b0a8-a933ac8701fb   
79   184057 -0.161130  51.54099  6f2b6908-f4c5-41fb-9dcd-93ffdeb50133   
96   186468 -0.275680  51.56441  ffae9bab-defd-4e91-bda5-358ec0e966c0   
117  161976  0.779530  51.32387  47d478c4-c251-462a-a68d-272e30f3dbc0   
134  334967 -3.815590  52.89826  d44ddace-5801-4039-bfff-86114e3666ab   
74   181586  0.334902  51.50994  98881a1f-4df9-4b62-9376-d8f6eaa107a7   

                                              geometry ITL_code  \
84   MULTIPOLYGON (((0.00114 51.50413, 0.00274 51.5...    TLI42   
38   POLYGON ((-1.38826 52.90147, -1.40277 52.90046...    TLF11   
89   MULTIPOLYGON (((0.13231 51.51188, 0.12442 51.5...    TLI52   
92   POLYGON ((0.07537 51.43199, 0.10703 51.41426, ...    TLI61   
88   MULTIPOLYGON (((-0.01533 51.48602, -0.01712 51...    TLI51   
177  POLYGON ((-5.86723 54.6888, -5.88878 54.69586,...    TLN0F   
98   POLYGON ((-0.30446 51.63635, -0.26713 51.60037...    TLI74   
76   POLYGON ((0.28601 52.09041, 0.32467 52.07278, ...    TLH35   
57   POLYGON ((-1.59549 52.45592, -1.59523 52.43993...    TLG32   
94   POLYGON ((-0.19002 51.44147, -0.18191 51.42474...    TLI63   
90   POLYGON ((0.02182 51.62883, 0.07283 51.60469, ...    TLI53   
99   POLYGON ((-0.28076 51.50285, -0.26765 51.49394...    TLI75   
83   MULTIPOLYGON (((0.0

In [307]:
df.value.describe()

count    179.000000
mean      -0.998227
std        0.003291
min       -1.008136
25%       -0.999978
50%       -0.998216
75%       -0.996577
max       -0.986925
Name: value, dtype: float64

In [ ]:
df = pd.read_excel("labourproductivityitls.xls", sheet_name="A4", skiprows=4)
df = df.melt(id_vars=["ITL_level", "ITL_code", "Region_name"], var_name="year", value_name="value")
df = df.dropna(subset=["value"])
df['year'] = df['year'].str[-4:].astype(int)
uk_val = df.query("ITL_code == 'UKX' and year == 2022")['value'].values[0]
df = df.query("ITL_level == 'ITL3'")


df = itl3_base.merge(df, left_on="ITL321CD", right_on="ITL_code", how="left")
df['value'] = df['value']/uk_val
df = df.query("year == 2022")

df['value'] = df['value']-1

df['rank'] = df['value'].rank(method='min', ascending=False)
point_num = 8
df['top_or_bottom_ten'] = np.where((df['rank'] <= point_num )| (df['rank'] > (len(df) - point_num)), True, False)



# 

In [262]:
df.query("country == 'Northern Ireland'")

ITL_level ITL_code                           Region_name  year  value  \
4525      ITL3    TLN06                               Belfast  2022   37.4   
4526      ITL3    TLN07  Armagh City, Banbridge and Craigavon  2022   31.6   
4527      ITL3    TLN08                Newry, Mourne and Down  2022   34.9   
4528      ITL3    TLN09                   Ards and North Down  2022   38.0   
4529      ITL3    TLN0A               Derry City and Strabane  2022   36.7   
4530      ITL3    TLN0B                            Mid Ulster  2022   39.7   
4531      ITL3    TLN0C              Causeway Coast and Glens  2022   34.4   
4532      ITL3    TLN0D               Antrim and Newtownabbey  2022   40.1   
4533      ITL3    TLN0E               Lisburn and Castlereagh  2022   38.1   
4534      ITL3    TLN0F                   Mid and East Antrim  2022   38.4   
4535      ITL3    TLN0G                   Fermanagh and Omagh  2022   38.0   

     ITL1           country    jitter  top_within_country  \
4525  TLN  Northern Ireland -0.407736                 7.0   
4526  TLN  Northern Ireland -0.857981                11.0   
4527  TLN  Northern Ireland -0.118919                 9.0   
4528  TLN  Northern Ireland -0.442734                 5.0   
4529  TLN  Northern Ireland  0.006346                 8.0   
4530  TLN  Northern Ireland -0.402767                 2.0   
4531  TLN  Northern Ireland -1.494762                10.0   
4532  TLN  Northern Ireland -0.570221                 1.0   
4533  TLN  Northern Ireland  0.528582                 4.0   
4534  TLN  Northern Ireland  1.592217                 3.0   
4535  TLN  Northern Ireland  0.197379                 5.0   

      bottom_within_country                                 label  
4525                    5.0                                        
4526                    1.0  Armagh City, Banbridge and Craigavon  
4527                    3.0                                        
4528                    7.0                                        
4529                    4.0                                        
4530                   10.0                            Mid Ulster  
4531                    2.0              Causeway Coast and Glens  
4532                   11.0               Antrim and Newtownabbey  
4533                    8.0                                        
4534                    9.0                                        
4535                    7.0

In [253]:
df.sort_values("value")

ITL_level ITL_code                Region_name  year  value ITL1  \
4493      ITL3    TLL24                      Powys  2022   26.1  TLL   
4477      ITL3    TLK42                     Torbay  2022   27.7  TLK   
4482      ITL3    TLL12                    Gwynedd  2022   27.8  TLL   
4362      ITL3    TLF15      North Nottinghamshire  2022   28.5  TLF   
4501      ITL3    TLM64         Na h-Eileanan Siar  2022   28.9  TLM   
...        ...      ...                        ...   ...    ...  ...   
4455      ITL3    TLJ37            North Hampshire  2022   60.7  TLJ   
4467      ITL3    TLK14                    Swindon  2022   61.0  TLK   
4412      ITL3    TLI32                Westminster  2022   64.5  TLI   
4417      ITL3    TLI42              Tower Hamlets  2022   68.4  TLI   
4411      ITL3    TLI31  Camden and City of London  2022   69.4  TLI   

       country    jitter  top_within_country  bottom_within_country  \
4493     Wales  0.615987                12.0                    1.0   
4477   England  0.208895               133.0                    1.0   
4482     Wales -1.947642                11.0                    2.0   
4362   England  1.258173               132.0                    2.0   
4501  Scotland -0.067746                23.0                    1.0   
...        ...       ...                 ...                    ...   
4455   England -0.508758                 5.0                  129.0   
4467   England -0.259212                 4.0                  130.0   
4412   England -0.010458                 3.0                  131.0   
4417   England  0.452951                 2.0                  132.0   
4411   England -0.615469                 1.0                  133.0   

                          label  
4493                      Powys  
4477                     Torbay  
4482                    Gwynedd  
4362      North Nottinghamshire  
4501         Na h-Eileanan Siar  
...                         ...  
4455                             
4467                             
4412                Westminster  
4417              Tower Hamlets  
4411  Camden and City of London  

[179 rows x 11 columns]

In [243]:
df.query("country == 'Wales'")

ITL_level ITL_code                     Region_name  year  value ITL1  \
4481      ITL3    TLL11                Isle of Anglesey  2022   33.0  TLL   
4482      ITL3    TLL12                         Gwynedd  2022   27.8  TLL   
4483      ITL3    TLL13          Conwy and Denbighshire  2022   29.1  TLL   
4484      ITL3    TLL14                South West Wales  2022   31.5  TLL   
4485      ITL3    TLL15                 Central Valleys  2022   33.4  TLL   
4486      ITL3    TLL16                   Gwent Valleys  2022   32.4  TLL   
4487      ITL3    TLL17  Bridgend and Neath Port Talbot  2022   35.4  TLL   
4488      ITL3    TLL18                         Swansea  2022   32.7  TLL   
4490      ITL3    TLL21       Monmouthshire and Newport  2022   36.6  TLL   
4491      ITL3    TLL22   Cardiff and Vale of Glamorgan  2022   36.3  TLL   
4492      ITL3    TLL23          Flintshire and Wrexham  2022   40.9  TLL   
4493      ITL3    TLL24                           Powys  2022   26.1  TLL   

     country    jitter  top_within_country  bottom_within_country label  
4481   Wales -1.006127                 6.0                    7.0        
4482   Wales  0.164736                11.0                    2.0        
4483   Wales  0.571039                10.0                    3.0        
4484   Wales -0.759699                 9.0                    4.0        
4485   Wales  0.716497                 5.0                    8.0        
4486   Wales -1.750756                 8.0                    5.0        
4487   Wales -0.779283                 4.0                    9.0        
4488   Wales -0.047003                 7.0                    6.0        
4490   Wales -1.376564                 2.0                   11.0        
4491   Wales -0.886426                 3.0                   10.0        
4492   Wales -1.566680                 1.0                   12.0        
4493   Wales -0.496973                12.0                    1.0

In [ ]:
df.sort_values("value", ascending=False).query("")

ITL_level ITL_code                   Region_name  year  value ITL1  \
4410      ITL2     TLI3           Inner London - West  2022   62.9  TLI   
4171      ITL2     TLI3           Inner London - West  2021   59.1  TLI   
3932      ITL2     TLI3           Inner London - West  2020   58.5  TLI   
3693      ITL2     TLI3           Inner London - West  2019   54.7  TLI   
3454      ITL2     TLI3           Inner London - West  2018   53.8  TLI   
...        ...      ...                           ...   ...    ...  ...   
649       ITL2     TLK3  Cornwall and Isles of Scilly  2006   20.6  TLK   
1127      ITL2     TLK3  Cornwall and Isles of Scilly  2008   20.5  TLK   
46        ITL2     TLE3               South Yorkshire  2004   20.2  TLE   
222       ITL2     TLN0              Northern Ireland  2004   20.1  TLN   
171       ITL2     TLK3  Cornwall and Isles of Scilly  2004   20.0  TLK   

               country    jitter  
4410           England  1.551244  
4171           England  0.147265  
3932           England  0.472357  
3693           England  0.369526  
3454           England  0.086080  
...                ...       ...  
649            England  1.689398  
1127           England -0.289882  
46             England  0.183883  
222   Northern Ireland  1.135706  
171            England -0.183663  

[779 rows x 8 columns]

In [168]:
df.sort_values(by='value', ascending=False)

OBJECTID ITL321CD                   ITL321NM   BNG_E   BNG_N     LONG  \
1519        80    TLI31  Camden and City of London  527620  184057 -0.16113   
1614        85    TLI42              Tower Hamlets  536345  181451 -0.03640   
1538        81    TLI32                Westminster  528268  180871 -0.15295   
2374       125    TLK14                    Swindon  418551  186564 -1.73367   
2203       116    TLJ37            North Hampshire  463331  151423 -1.09379   
...        ...      ...                        ...     ...     ...      ...   
2849       150    TLM64         Na h-Eileanan Siar  126473  932862 -6.65722   
816         43    TLF15      North Nottinghamshire  466570  368833 -1.00462   
2564       135    TLL12                    Gwynedd  277968  334967 -3.81559   
2507       132    TLK42                     Torbay  289730   64608 -3.55523   
2754       145    TLL24                      Powys  302328  273254 -3.43533   

           LAT                              GlobalID  \
1519  51.54099  6f2b6908-f4c5-41fb-9dcd-93ffdeb50133   
1614  51.51553  0a15a79e-bd9e-412e-af48-1c9065791af1   
1538  51.51221  3e050c3d-3b32-4a80-8432-316ec9a2a7fb   
2374  51.57763  eb3df646-6341-4a55-8325-2eb3f71eb7c9   
2203  51.25846  5fef0d34-09fe-46dc-9708-be3ba1003151   
...        ...                                   ...   
2849  58.19938  5096c6b2-2898-401d-abdd-4c5811fa057c   
816   53.21241  c28d35ae-0c60-4c52-9ac5-59eaaf79800d   
2564  52.89826  d44ddace-5801-4039-bfff-86114e3666ab   
2507  50.47088  eac4e77d-b4ca-4ff1-a9be-0ef01e2985b7   
2754  52.34863  01cf378f-64ba-408c-b72d-1220ab563955   

                                               geometry ITL_level ITL_code  \
1519  POLYGON ((-0.14239 51.56912, -0.12253 51.53073...      ITL3    TLI31   
1614  MULTIPOLYGON (((0.00114 51.50413, 0.00274 51.5...      ITL3    TLI42   
1538  POLYGON ((-0.11158 51.51534, -0.11144 51.50977...      ITL3    TLI32   
2374  POLYGON ((-1.68306 51.69011, -1.70019 51.67074...      ITL3    TLK14   
2203  POLYGON ((-1.08662 51.38392, -1.05002 51.35815...      ITL3    TLJ37   
...                                                 ...       ...      ...   
2849  MULTIPOLYGON (((-5.84204 59.11741, -5.84555 59...      ITL3    TLM64   
816   POLYGON ((-0.92025 53.46551, -0.91625 53.4603,...      ITL3    TLF15   
2564  MULTIPOLYGON (((-4.20949 53.20283, -4.20948 53...      ITL3    TLL12   
2507  POLYGON ((-3.50897 50.51661, -3.50903 50.51651...      ITL3    TLK42   
2754  POLYGON ((-3.1475 52.89017, -3.13552 52.88501,...      ITL3    TLL24   

                    Region_name  year     value   rank  top_or_bottom_ten  \
1519  Camden and City of London  2022  0.692683    1.0               True   
1614              Tower Hamlets  2022  0.668293    2.0               True   
1538                Westminster  2022  0.573171    3.0               True   
2374                    Swindon  2022  0.487805    4.0               True   
2203            North Hampshire  2022  0.480488    5.0               True   
...                         ...   ...       ...    ...                ...   
2849         Na h-Eileanan Siar  2022 -0.295122  175.0               True   
816       North Nottinghamshire  2022 -0.304878  176.0               True   
2564                    Gwynedd  2022 -0.321951  177.0               True   
2507                     Torbay  2022 -0.324390  178.0               True   
2754                      Powys  2022 -0.363415  179.0               True   

                 label_text  
1519                 LONDON  
1614          TOWER HAMLETS  
1538            WESTMINSTER  
2374                SWINDON  
2203            N HAMPSHIRE  
...                     ...  
2849  [NA H-EILEANAN, SIAR]  
816      N. NOTTINGHAMSHIRE  
2564                GWYNEDD  
2507                 TORBAY  
2754                  POWYS  

[179 rows x 17 columns]

In [104]:
"foo".upper()

'FOO'

In [51]:
df.value.describe()

count    179.000000
mean      -0.058114
std        0.173385
min       -0.363415
25%       -0.153659
50%       -0.104878
75%       -0.004878
max        0.692683
Name: value, dtype: float64

In [74]:
df.sort_values(by="value", ascending=True).head(20)

OBJECTID ITL321CD                              ITL321NM   BNG_E   BNG_N  \
2754       145    TLL24                                 Powys  302328  273254   
2507       132    TLK42                                Torbay  289730   64608   
2564       135    TLL12                               Gwynedd  277968  334967   
816         43    TLF15                 North Nottinghamshire  466570  368833   
2849       150    TLM64                    Na h-Eileanan Siar  126473  932862   
2583       136    TLL13                Conwy and Denbighshire  293490  357583   
626         33    TLE31     Barnsley, Doncaster and Rotherham  451623  398663   
303         16    TLD42                             Blackpool  332763  436633   
1405        74    TLH31                       Southend-on-Sea  587776  186833   
1177        62    TLG38                               Walsall  402098  300804   
56           3    TLC13                            Darlington  428029  515649   
151          8    TLD11                          West Cumbria  315410  516775   
911         48    TLF25                North Northamptonshire  493590  281718   
1139        60    TLG36                                Dudley  393191  288584   
2602       137    TLL14                      South West Wales  250540  245213   
949         50    TLG11              Herefordshire, County of  349434  242834   
2013       106    TLJ22                        East Sussex CC  564120  118026   
3229       170    TLN07  Armagh City, Banbridge and Craigavon  112171  508143   
37           2    TLC12                        South Teesside  461718  519597   
797         42    TLF14                            Nottingham  456082  339969   

          LONG       LAT                              GlobalID  \
2754 -3.435330  52.34863  01cf378f-64ba-408c-b72d-1220ab563955   
2507 -3.555230  50.47088  eac4e77d-b4ca-4ff1-a9be-0ef01e2985b7   
2564 -3.815590  52.89826  d44ddace-5801-4039-bfff-86114e3666ab   
816  -1.004620  53.21241  c28d35ae-0c60-4c52-9ac5-59eaaf79800d   
2849 -6.657220  58.19938  5096c6b2-2898-401d-abdd-4c5811fa057c   
2583 -3.592400  53.10478  3e36a80c-9374-491c-9237-00200c5e32a1   
626  -1.223560  53.48218  da632994-b7c4-45a1-ad8d-da9c847d0391   
303  -3.022840  53.82161  c05f1367-10ef-42ff-81cd-8d66f3b14c09   
1405  0.706906  51.54914  43e893e9-330e-4764-8923-9846cef9de8b   
1177 -1.970440  52.60503  c88727cc-996f-4101-b9bf-b27e4c302cdb   
56   -1.568350  54.53535  19f6e0b6-1047-45eb-972b-b76c9c720bcf   
151  -3.308940  54.53915  7a2e065c-fe26-4d56-b05d-bf3af71fdf15   
911  -0.625040  52.42546  0390d35e-f7a7-4dc8-ae4b-1e1db6aa64e9   
1139 -2.101710  52.49513  a5ad93ef-f134-481b-bca6-c4f7312ac149   
2602 -4.182740  52.08504  ba694947-fd57-4702-b5e0-1875ec520a33   
949  -2.739310  52.08154  351158d7-7cfc-4186-a16d-28e4d6d0ffed   
2013  0.334530  50.93832  5027920a-0ce8-43e3-8a3b-481c13c5fe7c   
3229 -6.433600  54.38660  c23bec02-bd77-4d64-bb11-c620722ca038   
37   -1.046950  54.56785  9e67f60c-56d9-4d92-99d9-b8751a251f1a   
797  -1.166670  52.95419  889678e6-12c2-41a0-b2c4-2f6eaeb0f8cc   

                                               geometry ITL_level ITL_code  \
2754  POLYGON ((-3.1475 52.89017, -3.13552 52.88501,...      ITL3    TLL24   
2507  POLYGON ((-3.50897 50.51661, -3.50903 50.51651...      ITL3    TLK42   
2564  MULTIPOLYGON (((-4.20949 53.20283, -4.20948 53...      ITL3    TLL12   
816   POLYGON ((-0.92025 53.46551, -0.91625 53.4603,...      ITL3    TLF15   
2849  MULTIPOLYGON (((-5.84204 59.11741, -5.84555 59...      ITL3    TLM64   
2583  POLYGON ((-3.36818 53.33524, -3.38835 53.32323...      ITL3    TLL13   
626   POLYGON ((-0.86534 53.63771, -0.89793 53.58328...      ITL3    TLE31   
303   POLYGON ((-3.01065 53.82619, -2.995 53.81849, ...      ITL3    TLD42   
1405  POLYGON ((0.82116 51.54061, 0.78763 51.52179, ...      ITL3    TLH31   
1177  POLYGON ((-1.87256 52.58494, -1.87872 52.56943...      ITL3    TLG38   
56    POLYGON ((-1.43836 54.59508, -1.42333 54.60313...    

## MAP: Growth in Productivity by region, 2022

In [22]:
df = full_itl3_df.copy()

102.5

In [31]:
uk_val = full_df.query("ITL_code == 'UKX' and year == 2022")['value'].values[0]

df = itl3_base.merge(full_itl3_df, left_on="ITL321CD", right_on="ITL_code", how="left")
df['value'] = df['value']/uk_val
df = df.query("year == 2022")



choropleth = alt.Chart(df).mark_geoshape().encode(
    color=alt.Color("value:Q", scale=alt.Scale(scheme="blues"), title="Labour Productivity (GBP per hour worked)"),
    tooltip=[
        alt.Tooltip("Region_name:N", title="Region"),
        alt.Tooltip("value:Q", title="Labour Productivity (GBP per hour worked)"),
    ]
)

choropleth

/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/finn/anaconda3/envs/workshop/lib/python3.11/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=Fa

alt.Chart(...)

In [ ]:
map